In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

import folium # map rendering library

In [2]:
df=pd.read_excel("capitals_2.xlsx")
points=pd.read_excel("temp.xlsx")

In [3]:
df.head()

Country/Territory   Capital  Population  Year % ofcountry'spopulation  \
0          China PR   Beijing    21542000  2010                    1.5%   
1             Japan     Tokyo    13929286  2017                  11.03%   
2            Russia    Moscow    12506468  2011                   8.52%   
3          DR Congo  Kinshasa    11855000  2012                   12.9%   
4         Indonesia   Jakarta    10075310  2011                   3.76%   

    Latitude   Longitude  CountVenue  RadiusRequest  
0  39.906217  116.391276        1100           2000  
1  35.682839  139.759455         700            500  
2  55.479205   37.327330         700          16000  
3  -4.321706   15.312597          34         100000  
4  -6.175394  106.827183         500           2000

In [4]:
points.head()

Capital   Latitude   Longitude  RadiusRequest  Count
0  Beijing  39.906217  116.391276           2000    100
1  Beijing  39.906217  116.355344           2000     69
2  Beijing  39.906217  116.427207           2000    100
3  Beijing  39.870285  116.391276           2000     46
4  Beijing  39.942149  116.391276           2000    100

In [5]:
with open("Foursquare.txt","r") as file1:
    CLIENT_ID = file1.readline()
    CLIENT_ID = CLIENT_ID[:(-1)] #delete "/n" from readline
    CLIENT_SECRET = file1.readline()
VERSION = "20200101"
LIMIT=100

In [6]:
def getNearbyVenues(names, latitudes, longitudes, radiuses):
    
    venues_list=[]
    for name, lat, lng, radius in zip(names, latitudes, longitudes, radiuses):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
        CLIENT_ID, 
        CLIENT_SECRET, 
        VERSION, 
        lat, 
        lng, 
        radius, 
        LIMIT)
            
        # make the GET request        
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
            
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Capital', 
                  'Capital Latitude', 
                  'Capital Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [8]:
capital_venues = getNearbyVenues(names=points['Capital'],
                                   latitudes=points['Latitude'],
                                   longitudes=points['Longitude'],
                                   radiuses=points["RadiusRequest"]
                                  )

Beijing
Beijing
Beijing
Beijing
Beijing
Beijing
Beijing
Beijing
Beijing
Tokyo
Tokyo
Tokyo
Tokyo
Tokyo
Tokyo
Tokyo
Moscow
Moscow
Moscow
Moscow
Moscow
Moscow
Moscow
Kinshasa
Jakarta
Jakarta
Jakarta
Jakarta
Jakarta
Seoul
Seoul
Seoul
Seoul
Seoul
Cairo
Cairo
Cairo
Cairo
Cairo
Mexico City
Mexico City
Mexico City
Mexico City
Mexico City
Dhaka
London
London
London
London
London
Lima
Lima
Lima
Lima
Lima
Tehran
Tehran
Tehran
Tehran
Tehran
Bangkok
Bangkok
Bangkok
Bangkok
Bangkok
Hanoi
Hanoi
Hanoi
Hanoi
Riyadh
Riyadh
Riyadh
Riyadh
Hong Kong
Hong Kong
Hong Kong
Hong Kong
Bogotá
Bogotá
Bogotá
Bogotá
Baghdad
Santiago
Santiago
Santiago
Santiago
Singapore
Singapore
Singapore
Ankara
Ankara
Ankara
Berlin
Berlin
Damascus
Algiers
Madrid
Madrid
Pyongyang
Kabul
Nairobi
Nairobi
Addis Ababa
Buenos Aires
Buenos Aires
Rome
Rome
Kiev
Kiev
Yaoundé
Taipei
Taipei
Brasília
Brasília
Amman
Amman
Luanda
Pretoria
Pretoria
Paris
Paris
Tashkent
Tashkent
Baku
Baku
Havana
Phnom Penh
Bucharest
Caracas
Brazzaville
Rabat
Manila

In [9]:
print(capital_venues.shape)
capital_venues.head()

(23199, 7)


Capital  Capital Latitude  Capital Longitude  \
0  Beijing         39.906217         116.391276   
1  Beijing         39.906217         116.391276   
2  Beijing         39.906217         116.391276   
3  Beijing         39.906217         116.391276   
4  Beijing         39.906217         116.391276   

                                             Venue  Venue Latitude  \
0                         Tian'anmen Tower (天安门城楼)       39.906562   
1                                               端门       39.908694   
2             Zhongshan Park (Zhongshan Park 中山公园)       39.908765   
3                        Tian'anmen Square (天安门广场)       39.904848   
4  National Centre for the Performing Arts (国家大剧院)       39.903936   

   Venue Longitude         Venue Category  
0       116.391582          Historic Site  
1       116.391192          Historic Site  
2       116.388602                   Park  
3       116.391306                  Plaza  
4       116.383541  Performing Arts Venue

In [10]:
capital_venues.groupby('Capital').count()

Capital Latitude  Capital Longitude  Venue  \
Capital                                                                 
Abu Dhabi                               100                100    100   
Abuja                                    58                 58     58   
Accra                                    82                 82     82   
Adamstown                                 1                  1      1   
Addis Ababa                              40                 40     40   
Algiers                                  65                 65     65   
Alofi                                     5                  5      5   
Amman                                   199                199    199   
Amsterdam                               100                100    100   
Andorra la Vella                        100                100    100   
Ankara                                  203                203    203   
Antananarivo                             41                 41     41   
Apia                                     13                 13     13   
Ashgabat                                100                100    100   
Asmara                                    4                  4      4   
Asunción                                100                100    100   
Athens                                  100                100    100   
Avarua                                    7                  7      7   
Baghdad                                  67                 67     67   
Baku                                    200                200    200   
Bamako                                   17                 17     17   
Bandar Seri Begawan                     100                100    100   
Bangkok                                 391                391    391   
Bangui                                    6                  6      6   
Banjul                                   31                 31     31   
Basseterre                              100                100    100   
Beijing                                 654                654    654   
Beirut                                  100                100    100   
Belfast                                 100                100    100   
Belgrade                                100                100    100   
Belmopan                                 70                 70     70   
Berlin                                  200                200    200   
Berne                                   100                100    100   
Bishkek                                  98                 98     98   
Bissau                                    7                  7      7   
Bogotá                                  158                158    158   
Brades                                   95                 95     95   
Brasília                                150                150    150   
Bratislava                              100                100    100   
Brazzaville                              34                 34     34   
Bridgetown                              100                100    100   
Brussels                                100                100    100   
Bucharest                               100                100    100   
Budapest                                100                100    100   
Buenos Aires                            191                191    191   
Cairo                                   290                290    290   
Canberra                                100                100    100   
Caracas                                 100                100    100   
Cardiff                                 100                100    100   
Castries                                100                100    100   
Charlotte Amalie                        100                100    100   
Chişinău                                100                100    100   
City of San Marino                      100                100    100   
Cockburn Tow

In [11]:
print('There are {} uniques categories.'.format(len(capital_venues['Venue Category'].unique())))

There are 604 uniques categories.


In [12]:
# one hot encoding
capital_onehot = pd.get_dummies(capital_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
capital_onehot['Capital'] = capital_venues['Capital'] 

# move neighborhood column to the first column
fixed_columns = [capital_onehot.columns[-1]] + list(capital_onehot.columns[:-1])
capital_onehot = capital_onehot[fixed_columns]

capital_onehot.head()

Capital  ATM  Acai House  Accessories Store  Acehnese Restaurant  \
0  Beijing    0           0                  0                    0   
1  Beijing    0           0                  0                    0   
2  Beijing    0           0                  0                    0   
3  Beijing    0           0                  0                    0   
4  Beijing    0           0                  0                    0   

   Adult Boutique  Advertising Agency  Afghan Restaurant  African Restaurant  \
0               0                   0                  0                   0   
1               0                   0                  0                   0   
2               0                   0                  0                   0   
3               0                   0                  0                   0   
4               0                   0                  0                   0   

   Airport  Airport Food Court  Airport Lounge  Airport Service  \
0        0                   0               0                0   
1        0                   0               0                0   
2        0                   0               0                0   
3        0                   0               0                0   
4        0                   0               0                0   

   Airport Terminal  Alsatian Restaurant  American Restaurant  Amphitheater  \
0                 0                    0                    0             0   
1                 0                    0                    0             0   
2                 0                    0                    0             0   
3                 0                    0                    0             0   
4                 0                    0                    0             0   

   Antique Shop  Apres Ski Bar  Aquarium  Arcade  Arepa Restaurant  \
0             0              0         0       0                 0   
1             0              0         0       0                 0   
2             0              0         0       0                 0   
3             0              0         0       0                 0   
4             0              0         0       0                 0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Arts & Entertainment  Ash and Haleem Place  Asian Restaurant  \
0                     0                     0                 0   
1                     0                     0                 0   
2                     0                     0                 0   
3                     0                     0                 0   
4                     0                     0                 0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                   0           0                      0                    0   
1                   0           0                      0                    0   
2                   0           0                      0                    0   
3                   0           0                      0                    0   
4                   0           0                      0                    0   

   Auto Garage  Auto Workshop  Automotive Shop  Auvergne Restaurant  \
0            0              0                0                    0   
1            0              0                0                    0   
2            0              0                0                    0   
3            0              0                0                    0   
4            0              0                0                    0   

   BBQ Joint  Baby Store  Ba

In [13]:
capital_onehot.shape

(23199, 605)

In [14]:
capital_grouped = capital_onehot.groupby('Capital').mean().reset_index()
capital_grouped

Capital   ATM  Acai House  Accessories Store  \
0                    Abu Dhabi  0.00        0.00           0.000000   
1                        Abuja  0.00        0.00           0.000000   
2                        Accra  0.00        0.00           0.000000   
3                    Adamstown  0.00        0.00           0.000000   
4                  Addis Ababa  0.00        0.00           0.000000   
5                      Algiers  0.00        0.00           0.000000   
6                        Alofi  0.00        0.00           0.000000   
7                        Amman  0.00        0.00           0.000000   
8                    Amsterdam  0.00        0.00           0.000000   
9             Andorra la Vella  0.00        0.00           0.000000   
10                      Ankara  0.00        0.00           0.000000   
11                Antananarivo  0.00        0.00           0.000000   
12                        Apia  0.00        0.00           0.000000   
13                    Ashgabat  0.00        0.00           0.000000   
14                      Asmara  0.00        0.00           0.000000   
15                    Asunción  0.00        0.00           0.000000   
16                      Athens  0.00        0.00           0.000000   
17                      Avarua  0.00        0.00           0.000000   
18                     Baghdad  0.00        0.00           0.000000   
19                        Baku  0.00        0.00           0.000000   
20                      Bamako  0.00        0.00           0.000000   
21         Bandar Seri Begawan  0.00        0.00           0.000000   
22                     Bangkok  0.00        0.00           0.000000   
23                      Bangui  0.00        0.00           0.000000   
24                      Banjul  0.00        0.00           0.000000   
25                  Basseterre  0.00        0.00           0.000000   
26                     Beijing  0.00        0.00           0.000000   
27                      Beirut  0.00        0.00           0.010000   
28                     Belfast  0.00        0.00           0.000000   
29                    Belgrade  0.00        0.00           0.000000   
30                    Belmopan  0.00        0.00           0.000000   
31                      Berlin  0.00        0.00           0.000000   
32                       Berne  0.00        0.00           0.000000   
33                     Bishkek  0.00        0.00           0.000000   
34                      Bissau  0.00        0.00           0.000000   
35                      Bogotá  0.00        0.00           0.000000   
36                      Brades  0.00        0.00           0.000000   
37                    Brasília  0.00        0.00           0.013333   
38                  Bratislava  0.00        0.00           0.000000   
39                 Brazzaville  0.00        0.00           0.000000   
40                  Bridgetown  0.00        0.00           0.000000   
41                    Brussels  0.00        0.00           0.000000   
42                   Bucharest  0.00        0.00           0.000000   
43                    Budapest  0.00        0.00           0.000000   
44                Buenos Aires  0.00        0.00           0.000000   
45                       Cairo  0.00        0.00           0.000000   
46                    Canberra  0.00        0.00           0.000000   
47                     Caracas  0.00        0.00           0.000000   
48                     Cardiff  0.00        0.00           0.000000   
49                    Castries  0.00        0.00           0.000000   
50            Charlotte Amalie  0.00        0.00           0.000000   
51                    Chişinău  0.00        0.00           0.000000   
52          City of San Marino  0.00        0.00           0.000000   
53               Cockburn Town  0.00        0.00           0.000000   
54                     Conakry  0.00        0.00           0.000000   
55                  Copenhagen  0.00        0.0

In [15]:
capital_grouped.shape

(242, 605)

In [16]:
num_top_venues = 5

for hood in capital_grouped['Capital']:
    print("----"+hood+"----")
    temp = capital_grouped[capital_grouped['Capital'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Abu Dhabi----
                  venue  freq
0                  Café  0.10
1           Coffee Shop  0.07
2            Restaurant  0.05
3  Fast Food Restaurant  0.05
4                 Hotel  0.04


----Abuja----
                  venue  freq
0                 Hotel  0.07
1         Shopping Mall  0.07
2  Fast Food Restaurant  0.07
3     Indian Restaurant  0.05
4            Restaurant  0.03


----Accra----
                venue  freq
0               Hotel  0.13
1       Shopping Mall  0.07
2              Resort  0.05
3  African Restaurant  0.05
4        Cocktail Bar  0.04


----Adamstown----
                   venue  freq
0        Nature Preserve   1.0
1                    ATM   0.0
2  Performing Arts Venue   0.0
3                Parking   0.0
4             Pastelaria   0.0


----Addis Ababa----
                  venue  freq
0                 Hotel  0.22
1    Italian Restaurant  0.12
2  Ethiopian Restaurant  0.10
3                  Café  0.08
4            Restaurant  0.08


----Algiers-

4  Sculpture Garden  0.03


----Djibouti (city)----
        venue  freq
0  Restaurant  0.15
1       Hotel  0.10
2  Hotel Pool  0.05
3   Nightclub  0.05
4      Lounge  0.05


----Dodoma----
                 venue  freq
0                Hotel  0.50
1          Pizza Place  0.25
2  Rental Car Location  0.25
3                  ATM  0.00
4        Pelmeni House  0.00


----Doha----
                       venue  freq
0                      Hotel  0.12
1                       Café  0.09
2  Middle Eastern Restaurant  0.08
3                Coffee Shop  0.04
4                 Restaurant  0.04


----Douglas----
         venue  freq
0   Restaurant  0.10
1          Pub  0.06
2          Bar  0.06
3  Coffee Shop  0.05
4         Park  0.05


----Dublin----
            venue  freq
0             Pub  0.17
1     Coffee Shop  0.10
2            Café  0.07
3  Clothing Store  0.04
4      Restaurant  0.04


----Dushanbe----
                       venue  freq
0                      Hotel  0.18
1                 

4  Fried Chicken Joint  0.04


----Lisbon----
                   venue  freq
0  Portuguese Restaurant  0.14
1                  Plaza  0.08
2             Restaurant  0.05
3                  Hotel  0.05
4               Wine Bar  0.04


----Ljubljana----
         venue  freq
0   Restaurant  0.07
1        Plaza  0.05
2  Pizza Place  0.05
3        Hotel  0.05
4         Café  0.05


----Lomé----
                venue  freq
0               Hotel  0.25
1          Restaurant  0.10
2              Bakery  0.05
3  Spanish Restaurant  0.05
4       Grocery Store  0.05


----London----
            venue  freq
0         Theater  0.06
1           Hotel  0.05
2     Coffee Shop  0.04
3  Sandwich Place  0.03
4      Restaurant  0.03


----Longyearbyen----
            venue  freq
0           Hotel  0.26
1             Bar  0.17
2  Boarding House  0.04
3      Restaurant  0.04
4            Café  0.04


----Luanda----
         venue  freq
0   Restaurant  0.23
1        Beach  0.09
2  Pizza Place  0.07
3        H

4                Bookstore  0.04


----Ottawa----
              venue  freq
0       Coffee Shop  0.10
1             Hotel  0.05
2              Café  0.04
3        Restaurant  0.03
4  Tapas Restaurant  0.03


----Ouagadougou----
                 venue  freq
0                Hotel  0.27
1       Breakfast Spot  0.09
2              Airport  0.09
3  Lebanese Restaurant  0.09
4            Nightclub  0.09


----Pago Pago----
                 venue  freq
0       Breakfast Spot   0.2
1  American Restaurant   0.2
2        Movie Theater   0.2
3           Food Court   0.2
4              Stadium   0.2


----Palikir----
        venue  freq
0       Hotel  0.75
1     Airport  0.25
2         ATM  0.00
3     Parking  0.00
4  Pastelaria  0.00


----Panama City----
                venue  freq
0               Hotel  0.16
1          Restaurant  0.07
2                 Bar  0.06
3  Italian Restaurant  0.05
4    Greek Restaurant  0.04


----Papeete----
               venue  freq
0  French Restaurant  0.24
1   

            venue  freq
0            Café  0.26
1           Hotel  0.23
2  Scenic Lookout  0.08
3     Pizza Place  0.03
4        Tea Room  0.03


----Tórshavn----
                     venue  freq
0                     Café  0.12
1                    Hotel  0.12
2  Scandinavian Restaurant  0.10
3               Lighthouse  0.07
4               Steakhouse  0.05


----Ulaanbaatar----
                  venue  freq
0           Coffee Shop  0.16
1                 Hotel  0.13
2            Soup Place  0.03
3  Fast Food Restaurant  0.03
4   Japanese Restaurant  0.03


----Vaduz----
              venue  freq
0             Hotel  0.17
1        Restaurant  0.10
2  Swiss Restaurant  0.07
3              Café  0.05
4       Supermarket  0.04


----Valletta----
                      venue  freq
0  Mediterranean Restaurant  0.13
1        Italian Restaurant  0.08
2                Restaurant  0.06
3                       Bar  0.06
4                      Café  0.05


----Vatican City----
                ven

In [17]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [18]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Capital']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

In [19]:


# create a new dataframe
capitals_venues_sorted = pd.DataFrame(columns=columns)
capitals_venues_sorted['Capital'] = capital_grouped['Capital']

for ind in np.arange(capital_grouped.shape[0]):
    capitals_venues_sorted.iloc[ind, 1:] = return_most_common_venues(capital_grouped.iloc[ind, :], num_top_venues)

capitals_venues_sorted.head()

Capital 1st Most Common Venue 2nd Most Common Venue  \
0    Abu Dhabi                  Café           Coffee Shop   
1        Abuja                 Hotel         Shopping Mall   
2        Accra                 Hotel         Shopping Mall   
3    Adamstown       Nature Preserve           Zoo Exhibit   
4  Addis Ababa                 Hotel    Italian Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0            Restaurant  Fast Food Restaurant                 Hotel   
1  Fast Food Restaurant     Indian Restaurant         Movie Theater   
2                Resort    African Restaurant          Cocktail Bar   
3    Falafel Restaurant     Fish & Chips Shop   Filipino Restaurant   
4  Ethiopian Restaurant                  Café            Restaurant   

  6th Most Common Venue       7th Most Common Venue 8th Most Common Venue  \
0    Italian Restaurant                 Pizza Place     Indian Restaurant   
1    Chinese Restaurant                      Arcade       Bed & Breakfast   
2                  Café  Modern European Restaurant         Movie Theater   
3                 Field        Fast Food Restaurant        Farmers Market   
4           Pizza Place                   Nightclub   American Restaurant   

  9th Most Common Venue     10th Most Common Venue  
0                   Spa                        Bar  
1      Department Store             Ice Cream Shop  
2           Pizza Place           Department Store  
3                  Farm                       Fair  
4           Coffee Shop  Middle Eastern Restaurant

In [20]:
# set number of clusters
kclusters = 5

capital_grouped_clustering = capital_grouped.drop('Capital', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(capital_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([3, 3, 3, 4, 3, 3, 1, 3, 3, 3])

In [21]:
# add clustering labels
capitals_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

capital_merged = df

capital_merged.head()

Country/Territory   Capital  Population  Year % ofcountry'spopulation  \
0          China PR   Beijing    21542000  2010                    1.5%   
1             Japan     Tokyo    13929286  2017                  11.03%   
2            Russia    Moscow    12506468  2011                   8.52%   
3          DR Congo  Kinshasa    11855000  2012                   12.9%   
4         Indonesia   Jakarta    10075310  2011                   3.76%   

    Latitude   Longitude  CountVenue  RadiusRequest  
0  39.906217  116.391276        1100           2000  
1  35.682839  139.759455         700            500  
2  55.479205   37.327330         700          16000  
3  -4.321706   15.312597          34         100000  
4  -6.175394  106.827183         500           2000

In [22]:
capital_merged.shape

(243, 9)

In [23]:
capitals_venues_sorted.shape

(242, 12)

In [24]:
# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
capital_merged = capital_merged.join(capitals_venues_sorted.set_index('Capital'), on='Capital')

capital_merged.head() # check the last columns!

Country/Territory   Capital  Population  Year % ofcountry'spopulation  \
0          China PR   Beijing    21542000  2010                    1.5%   
1             Japan     Tokyo    13929286  2017                  11.03%   
2            Russia    Moscow    12506468  2011                   8.52%   
3          DR Congo  Kinshasa    11855000  2012                   12.9%   
4         Indonesia   Jakarta    10075310  2011                   3.76%   

    Latitude   Longitude  CountVenue  RadiusRequest  Cluster Labels  \
0  39.906217  116.391276        1100           2000               3   
1  35.682839  139.759455         700            500               3   
2  55.479205   37.327330         700          16000               3   
3  -4.321706   15.312597          34         100000               3   
4  -6.175394  106.827183         500           2000               3   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0                 Hotel           Coffee Shop    Chinese Restaurant   
1                  Café   Japanese Restaurant         Historic Site   
2                  Park  Gym / Fitness Center            Restaurant   
3                 Hotel                  Café            Restaurant   
4           Coffee Shop                 Hotel    Chinese Restaurant   

   4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0          Historic Site  Fast Food Restaurant                  Café   
1            Coffee Shop      Ramen Restaurant              Sake Bar   
2            Supermarket                 Hotel           Coffee Shop   
3   Fast Food Restaurant                Lounge                 Diner   
4  Indonesian Restaurant          Noodle House      Asian Restaurant   

  7th Most Common Venue 8th Most Common Venue      9th Most Common Venue  \
0           Pizza Place                   Bar              Shopping Mall   
1     Convenience Store    Chinese Restaurant  Japanese Curry Restaurant   
2           Yoga Studio                  Café                     Resort   
3          Cocktail Bar                  Pool                      Plaza   
4    Seafood Restaurant                  Café       Fast Food Restaurant   

  10th Most Common Venue  
0                   Park  
1     Italian Restaurant  
2          Historic Site  
3            Pizza Place  
4            Pizza Place

In [25]:
print(capital_merged[["Capital","Cluster Labels"]].groupby("Cluster Labels").count(),"\n")

                Capital
Cluster Labels         
0                    33
1                     6
2                    29
3                   174
4                     1 



In [26]:
def Klastering(kclusters):
    # create a new dataframe
    capitals_venues_sorted = pd.DataFrame(columns=columns)
    capitals_venues_sorted['Capital'] = capital_grouped['Capital']

    for ind in np.arange(capital_grouped.shape[0]):
        capitals_venues_sorted.iloc[ind, 1:] = return_most_common_venues(capital_grouped.iloc[ind, :], num_top_venues)

    capital_grouped_clustering = capital_grouped.drop('Capital', 1)

    # run k-means clustering
    kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(capital_grouped_clustering)
    
    # add clustering labels
    capitals_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

    capital_merged = df
    
    # merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
    capital_merged = capital_merged.join(capitals_venues_sorted.set_index('Capital'), on='Capital')
    
    return capital_merged

In [27]:
for k in range(3,21):
    capital_merged = Klastering(k)
    print("For {} number of clusters:".format(k))
    print(capital_merged[["Capital","Cluster Labels"]].groupby("Cluster Labels").count(),"\n")

For 3 number of clusters:
                Capital
Cluster Labels         
0                     4
1                   210
2                    29 

For 4 number of clusters:
                Capital
Cluster Labels         
0                    48
1                     9
2                     1
3                   185 

For 5 number of clusters:
                Capital
Cluster Labels         
0                    33
1                     6
2                    29
3                   174
4                     1 

For 6 number of clusters:
                Capital
Cluster Labels         
0                    47
1                     3
2                     1
3                    38
4                   143
5                    11 

For 7 number of clusters:
                Capital
Cluster Labels         
0                    35
1                   133
2                    15
3                    53
4                     1
5                     1
6                     5 

For 8 number of clus

In [28]:
kclusters = 9
capital_merged = Klastering(kclusters)

In [29]:
# create map
map_clusters = folium.Map()

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(capital_merged['Latitude'], capital_merged['Longitude'], capital_merged['Capital'], capital_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [30]:
capital_merged.loc[capital_merged['Cluster Labels'] == 0, capital_merged.columns[[1,2] + list(range(5, capital_merged.shape[1]))]]

Capital  Population   Latitude   Longitude  CountVenue  \
68     Port-au-Prince     1235227  18.547327  -72.339593          65   
111          Kingston      701063  17.971215  -76.792813          92   
126             Macau      520400  -5.113366  -36.634996         100   
129      Yamoussoukro      454929   6.809107   -5.273263           7   
150            Nassau      248948  25.078346  -77.338333         100   
166        Bridgetown      110000  13.097783  -59.618418         100   
170            Nouméa       89207 -22.274526  166.442419          39   
175          Castries       70000  13.952589  -60.987824         100   
184        Willemstad       49885  12.109124  -68.931655         100   
186         Kingstown       40020  13.156186  -61.227962          91   
192        Oranjestad       29998  12.526874  -70.035685         100   
193          Victoria       29298  -4.623208   55.452359          95   
197       George Town       26798  19.295355  -81.380778          96   
199           Papeete       26200 -17.537384 -149.565996          59   
203        St. John's       22679  17.118457  -61.844851          65   
207          Belmopan       16451  17.250199  -88.770018          70   
209            Roseau       14847  15.299192  -61.387287         100   
210        Basseterre       13043  17.296092  -62.722301         100   
212  Charlotte Amalie       10817  18.341137  -64.932789         100   
214         Road Town        9400  18.425713  -64.623223         100   
217          Gustavia        6000  17.895704  -62.850837         100   
218           Marigot        5700  18.066854  -63.084887         100   
224     Cockburn Town        3700  21.460772  -71.139996          14   
228       Philipsburg        1338  18.025071  -63.048307         100   
230        The Valley        1169  18.214586  -63.051776         100   
232           Hagåtña        1100  13.472745  144.752018          89   
233          Hamilton        1010  32.295608  -64.782705          55   
234          Kingston         880  17.971215  -76.792813          92   
238            Brades         391  16.789060  -62.208731          17   

     RadiusRequest  Cluster Labels 1st Most Common Venue  \
68          100000               0                Resort   
111         100000               0                 Hotel   
126          64000               0                 Beach   
129         100000               0            Hotel Pool   
150           2000               0                Resort   
166           4000               0                   Bar   
170         100000               0                Resort   
175          16000               0                Resort   
184           4000               0                 Hotel   
186         100000               0  Caribbean Restaurant   
192           4000               0  Caribbean Restaurant   
193         100000               0                Resort   
197         100000               0  Caribbean Restaurant   
199         100000               0     French Restaurant   
203         100000               0                 Hotel   
207         100000               0                Resort   
209         128000               0                 Beach   
210         128000               0                 Beach   
212          16000               0                 Beach   
214          32000               0                 Beach   
217          32000               0     French Restaurant   
218           8000               0     French Restaurant   
224         100000               0  Caribbean Restaurant   
228          32000               0                 Beach   
230          64000               0                 Beach   
232         100000               0                 Hotel   
233         100000               0            Restaurant   
234         100000               0                 Hotel   
238         100000               0                 Beach   

    2nd Most Common Venue 3rd Most Common Venue 4th 

In [31]:
capital_merged.loc[capital_merged['Cluster Labels'] == 1, capital_merged.columns[[1,2] + list(range(5, capital_merged.shape[1]))]]

Capital  Population   Latitude   Longitude  CountVenue  \
16                Bogotá     7181469   4.598080  -74.076044         400   
21                Berlin     3748148  52.517037   13.388860         200   
22              Damascus     3500000  33.513070   36.309581         100   
23               Algiers     3415811  36.775361    3.060188          65   
24                Madrid     3233527  40.416705   -3.703582         200   
30                  Rome     2868104  41.893320   12.482932         200   
32               Yaoundé     2765568   3.868987   11.521334          38   
34              Brasília     2648532 -15.793889  -47.882778         200   
36                Luanda     2453779  -8.827270   13.243951          70   
41                Havana     2135498  23.135305  -82.358963          64   
48                Vienna     1749673  48.208354   16.372504         100   
54                 Accra     1640507   5.560014   -0.205744          82   
55          Antananarivo     1613375 -18.910012   47.525581          41   
58                Harare     1487028 -17.831773   31.045686          37   
63            Montevideo     1369797 -34.905904  -56.191357         100   
72              Belgrade     1154589  44.817813   20.456897         100   
75               Yerevan     1080487  40.177612   44.512585         100   
77              Freetown     1070200   8.479004  -13.267950          11   
79                 Dakar     1030594  14.693425  -17.447938          75   
80   Nur-Sultan (Astana)     1029556  51.128220   71.430668          86   
95           Panama City      813097   8.971449  -79.534180         100   
101                Abuja      778567   9.064331    7.489297          58   
103               Tirana      763634  41.315886   19.900912         100   
104             Ashgabat      763537  37.937832   58.235947         100   
110                 Riga      713016  56.949398   24.105185         100   
119               Lisbon      564657  38.707751   -9.136592         100   
122           Libreville      556425   0.390002    9.454001          22   
124               Skopje      521000  41.996092   21.431649         100   
127            Edinburgh      492680  55.953346   -3.188375         100   
128      Djibouti (city)      475332  11.814597   42.845306          20   
136             Sarajevo      395133  43.851977   18.386687         100   
139              Belfast      333871  54.596441   -5.930276         100   
144            Ljubljana      280140  46.049980   14.506860         100   
146               Maseru      267652 -29.310054   27.478222           6   
147                Sucre      261201 -19.047725  -65.259431          52   
152           Porto-Novo      223552   6.499072    2.625336         100   
153            Prishtina      198214  42.663877   21.164085         100   
155             Tiraspol      159163  46.837999   29.610954         100   
157           Port Louis      147251 -20.163728   57.504533         100   
162                Praia      125464  14.916017  -23.509613          21   
163                Berne      121631  46.948271    7.451451         100   
174           Luxembourg      119214  49.815868    6.129675         100   
176               Saipan       62392  15.190983  145.746853          44   
189               Monaco       35986  43.732349    7.427683         100   
198              Douglas       26600  54.235817   -4.514599         100   
202     Andorra la Vella       22884  42.506939    1.521247         100   
206       St. Peter Port       16701  49.456814   -2.538998         100   
211            Mariehamn       11296  60.102423   19.941260          74   
216             Valletta        6444  35.898982   14.513676         100   
220               Avarua        5445 -21.207474 -159.770815           7   
221                Vaduz        5248  47.139286    9.522796         100   
222   City of San Marino        4493  43.936400   12.446699         100   
235         Vatican City         826  41.9

In [32]:
capital_merged.loc[capital_merged['Cluster Labels'] == 2, capital_merged.columns[[1,2] + list(range(5, capital_merged.shape[1]))]]

Capital  Population   Latitude   Longitude  CountVenue  RadiusRequest  \
25   Pyongyang     3144005  39.019474  125.753388           6         100000   
61     Conakry     1399981   9.517060  -13.699843          13         100000   
112     Asmara      694000  15.338967   38.932676           4         100000   
130     Bissau      452640  11.861324  -15.583055           7         100000   
143     Dodoma      287200  -6.337282   35.737177           4         100000   
154   El Aaiún      194668  27.154512  -13.195392           4         100000   
180   São Tomé       56166   0.338924    6.731303           9         100000   
213    Palikir        9900   6.920744  158.162714           4         100000   
229   Mata-Utu        1191 -13.282042 -176.174022           2         100000   
231      Yaren        1100  -0.547101  166.916400           4         100000   

     Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
25                2                 Hotel                 Plaza   
61                2                 Hotel     French Restaurant   
112               2                 Hotel           Zoo Exhibit   
130               2                 Hotel                Bakery   
143               2                 Hotel           Pizza Place   
154               2                 Hotel                Resort   
180               2                 Hotel                  Café   
213               2                 Hotel               Airport   
229               2                 Hotel               Airport   
231               2                 Hotel      Department Store   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
25                Stadium               Airport                  Fair   
61     Mexican Restaurant     Electronics Store    Turkish Restaurant   
112    Falafel Restaurant     Fish & Chips Shop   Filipino Restaurant   
130            Restaurant               Airport                 Plaza   
143   Rental Car Location           Zoo Exhibit    Falafel Restaurant   
154    African Restaurant                  Fair   Filipino Restaurant   
180             BBQ Joint                   Bar               Airport   
213           Zoo Exhibit    Falafel Restaurant     Fish & Chips Shop   
229           Zoo Exhibit    Falafel Restaurant     Fish & Chips Shop   
231               Airport           Zoo Exhibit                  Farm   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
25    Filipino Restaurant                 Field  Fast Food Restaurant   
61                 Resort         Shopping Mall      Pedestrian Plaza   
112                 Field  Fast Food Restaurant        Farmers Market   
130                  Fair   Filipino Restaurant                 Field   
143   Filipino Restaurant                 Field  Fast Food Restaurant   
154                 Field  Fast Food Restaurant        Farmers Market   
180                  Farm     Fish & Chips Shop   Filipino Restaurant   
213   Filipino Restaurant                 Field  Fast Food Restaurant   
229   Filipino Restaurant                 Field  Fast Food Restaurant   
231     Fish & Chips Shop   Filipino Restaurant                 Field   

    9th Most Common Venue 10th Most Common Venue  
25         Farmers Market                   Farm  
61            Fabric Shop         Farmers Market  
112                  Farm                   Fair  
130  Fast Food Restaurant         Farmers Market  
143        Farmers Market                   Farm  
154                  Farm     Falafel Restaurant  
180                 Field   Fast Food Restaurant  
213        Farmers Market                   Farm  
229        Farmers Market                   Farm  
231  Fast Food Restaurant         Farmers Market

In [33]:
capital_merged.loc[capital_merged['Cluster Labels'] == 3, capital_merged.columns[[1,2] + list(range(5, capital_merged.shape[1]))]]

Capital  Population   Latitude   Longitude  CountVenue  RadiusRequest  \
241  Adamstown          56 -25.066667 -130.100205           3         100000   

     Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
241               3       Nature Preserve           Zoo Exhibit   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
241    Falafel Restaurant     Fish & Chips Shop   Filipino Restaurant   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
241                 Field  Fast Food Restaurant        Farmers Market   

    9th Most Common Venue 10th Most Common Venue  
241                  Farm                   Fair

In [34]:
capital_merged.loc[capital_merged['Cluster Labels'] == 4, capital_merged.columns[[1,2] + list(range(5, capital_merged.shape[1]))]]

Capital  Population  Latitude  Longitude  CountVenue  RadiusRequest  \
74  Mogadishu     1097133  2.042778  45.338564           8         100000   

    Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
74               4       Automotive Shop                 Beach   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
74                 Hotel           Zoo Exhibit    Falafel Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
74   Filipino Restaurant                 Field  Fast Food Restaurant   

   9th Most Common Venue 10th Most Common Venue  
74        Farmers Market                   Farm

In [35]:
capital_merged.loc[capital_merged['Cluster Labels'] == 5, capital_merged.columns[[1,2] + list(range(5, capital_merged.shape[1]))]]

Capital  Population   Latitude  Longitude  CountVenue  RadiusRequest  \
240  West Island         120 -12.189848  96.830449           1         100000   

     Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
240               5               Airport    Falafel Restaurant   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
240           Fish Market     Fish & Chips Shop   Filipino Restaurant   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
240                 Field  Fast Food Restaurant        Farmers Market   

    9th Most Common Venue 10th Most Common Venue  
240                  Farm            Zoo Exhibit

In [36]:
capital_merged.loc[capital_merged['Cluster Labels'] == 6, capital_merged.columns[[1,2] + list(range(5, capital_merged.shape[1]))]]

Capital  Population   Latitude   Longitude  CountVenue  \
3          Kinshasa    11855000  -4.321706   15.312597          34   
17          Baghdad     6719500  33.302431   44.378799          67   
26            Kabul     3140853  34.526013   69.177648          24   
28      Addis Ababa     3040740   9.010793   38.761252          40   
42       Phnom Penh     2011725  11.568271  104.922443         100   
45      Brazzaville     1827000  -4.269441   15.271226          34   
46            Rabat     1789635  34.022405   -6.834543         100   
53          Kampala     1659600   0.317714   32.581354          85   
59             Doha     1450000  25.285633   51.526416         100   
60           Sana'a     1431649  15.353857   44.205884          13   
64           Lusaka     1331254 -15.416449   28.282153          46   
69          Tripoli     1184045  32.896672   13.177792          39   
76           Maputo     1076689 -25.966213   32.567450          57   
81        Guatemala     1022000  15.635609  -89.898809          63   
86        Islamabad      955629  22.330800   91.841286          33   
91         Lilongwe      902388 -13.987511   33.768144          19   
98           Niamey      794814  13.524834    2.109823          18   
100       Jerusalem      927000  31.778345   35.225079         100   
102           Tunis      767629  33.843941    9.400138          39   
107          Bangui      731548   4.390715   18.550913           6   
108      Nouakchott      719167  18.079238  -15.978007          18   
109          Kigali      718414  -1.885960   30.129675          51   
118        Dushanbe      582496  38.542583   68.815214          44   
142       Vientiane      287579  17.964099  102.613371         100   
149        Windhoek      252721 -22.574392   17.079069          42   
151        Gaborone      225656 -24.658136   25.908847          49   
161      Georgetown      134599   6.802577  -58.162861          31   
173         Mbabane       81594 -26.325745   31.144663          43   
178         Honiara       59288  -9.431077  159.955255           4   
179            Dili       59069  -8.553681  125.578409          29   
183     Stepanakert       49986  39.824945   46.752259          49   
187            Apia       39813 -13.834369 -171.769279          13   
188       Port Vila       38000 -17.741497  168.315016          11   
195    Saint Helier       28380  47.384387    4.683325         100   
200        Ramallah       25500  31.903082   35.195174         100   
204      Nukuʻalofa       22400 -21.134340 -175.201808           8   
205        Tórshavn       18573  62.012000   -6.768000          42   
208  Nuuk (Godthåb)       15469  64.175029  -51.735539           5   
237           Alofi         616 -19.053416 -169.919199           5   

     RadiusRequest  Cluster Labels  1st Most Common Venue  \
3           100000               6                  Hotel   
17          100000               6                  Hotel   
26          100000               6                  Hotel   
28          100000               6                  Hotel   
42            1000               6                  Hotel   
45          100000               6                  Hotel   
46            1000               6                   Café   
53          100000               6                   Café   
59            2000               6                  Hotel   
60          100000               6                   Café   
64          100000               6                  Hotel   
69          100000               6                   Café   
76          100000               6                  Hotel   
81          100000               6                  Hotel   
86          100000               6          Shopping Mall   
91          100000               6                  Hotel   
98          100000               6                  Hotel   
100           1000               6                  Hotel   
102         100000               6                  

In [37]:
capital_merged.loc[capital_merged['Cluster Labels'] == 7, capital_merged.columns[[1,2] + list(range(5, capital_merged.shape[1]))]]

Capital  Population   Latitude   Longitude  CountVenue  \
65         Bamako     1289626  12.605033   -7.986514          17   
82       Monrovia     1010970   6.328034  -10.797788          22   
83    Ouagadougou     1005231  12.368148   -1.527085          11   
89      Naypyidaw      925000  19.754005   96.134498          20   
94           Lomé      824738   6.130419    1.215829          20   
105     N'Djamena      751288  12.119154   15.050276          12   
137          Juba      372410   4.847202   31.595166           7   
141  Port Moresby      299396  -9.474330  147.159950          14   
168       Thimphu      101259  27.472762   89.629548          50   
169        Malabo      100677   3.752828    8.780061           8   
177        Moroni       60200 -11.693126   43.254304           8   
185        Gitega       41944  -3.428495   29.924972          13   
190        Banjul       34828  13.441346  -16.562471          31   
201        Majuro       25400   7.090992  171.381635           4   
223      Funafuti        4492  -8.534995  179.118650           5   
226  Longyearbyen        2075  78.223156   15.646366          23   

     RadiusRequest  Cluster Labels 1st Most Common Venue  \
65          100000               7                 Hotel   
82          100000               7                 Hotel   
83          100000               7                 Hotel   
89          100000               7                 Hotel   
94          100000               7                 Hotel   
105         100000               7                 Hotel   
137         100000               7                 Hotel   
141         100000               7                 Hotel   
168         100000               7                 Hotel   
169         100000               7                 Hotel   
177         100000               7                 Hotel   
185         100000               7                 Hotel   
190         100000               7                 Hotel   
201         100000               7                   Bar   
223         100000               7                 Hotel   
226         100000               7                 Hotel   

    2nd Most Common Venue 3rd Most Common Venue    4th Most Common Venue  \
65            Pizza Place               Airport         Greek Restaurant   
82                Airport            Restaurant            Boat or Ferry   
83    Lebanese Restaurant    African Restaurant                     Pool   
89       Asian Restaurant         Shopping Mall               Hotel Pool   
94             Restaurant               Airport                    Diner   
105     French Restaurant    African Restaurant                  Airport   
137         Grocery Store                  Café               Restaurant   
141                Market       Harbor / Marina         Asian Restaurant   
168                  Café                Resort            Historic Site   
169                  Café     French Restaurant                Hotel Bar   
177                Resort    Falafel Restaurant           Adult Boutique   
185            Restaurant           Pizza Place                    Diner   
190                Resort                 River               Restaurant   
201             Hotel Bar                 Hotel                  Airport   
223       Bed & Breakfast                 Beach                  Airport   
226                   Bar               Airport  Scandinavian Restaurant   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
65                 Hostel         Grocery Store           Sports Club   
82          Grocery Store                  Café               Stadium   
83              Nightclub               Airport           Coffee Shop   
89                Airport                  Café      Department Store   
94     Spanish Restaurant         Grocery Store  Fast Food Restaurant   
105                Resort            Hotel Pool                Market   
137         Shopping Mall   

In [38]:
capital_merged.loc[capital_merged['Cluster Labels'] == 8, capital_merged.columns[[1,2] + list(range(5, capital_merged.shape[1]))]]

Capital  Population   Latitude   Longitude  CountVenue  \
0                      Beijing    21542000  39.906217  116.391276        1100   
1                        Tokyo    13929286  35.682839  139.759455         700   
2                       Moscow    12506468  55.479205   37.327330         700   
4                      Jakarta    10075310  -6.175394  106.827183         500   
5                        Seoul     9838892  37.564983  126.939211         500   
6                        Cairo     9500000  30.048819   31.243666         500   
7                  Mexico City     8918653  19.432630  -99.133178         500   
8                        Dhaka     8906039  23.759357   90.378814          60   
9                       London     8908081  51.507322   -0.127647         500   
10                        Lima     8852000 -12.062107  -77.036526         500   
11                      Tehran     8693706  35.700618   51.401378         500   
12                     Bangkok     8305218  13.754253  100.493087         500   
13                       Hanoi     7781631  21.029450  105.854444         400   
14                      Riyadh     7676654  24.631969   46.715065         400   
15                   Hong Kong     7482500  22.279328  114.162813         400   
18                    Santiago     6310000 -33.437797  -70.650445         400   
19                   Singapore     5638700   1.357107  103.819499         300   
20                      Ankara     5445026  39.716044   32.705995         300   
27                     Nairobi     3138369  -1.283253   36.817245         200   
29                Buenos Aires     2891082 -34.607568  -58.437089         200   
31                        Kiev     2847200  50.450034   30.524136         200   
33                      Taipei     2668572  25.037520  121.563680         200   
35                       Amman     2600603  31.951569   35.923963         200   
37                    Pretoria     2345908 -25.745937   28.187944         200   
38                       Paris     2241346  48.856697    2.351462         200   
39                    Tashkent     2207850  41.312336   69.278708         200   
40                        Baku     2204200  40.375443   49.832675         200   
43                   Bucharest     1942254  44.436141   26.102720         100   
44                     Caracas     1838939  10.506098  -66.914602         100   
47                      Manila     1780148  14.590622  120.979970         100   
49                    Khartoum     1840661  15.593325   32.535650          76   
50                    Budapest     1729040  47.481390   19.146073         100   
51                      Warsaw     1711324  52.233717   21.071411         100   
52                       Minsk     1702061  53.902334   27.561879         100   
56                      Beirut     1574387  33.895920   35.478430         100   
57                   Guayaquil     1504991  -2.189907  -79.887726         100   
62                Kuala Lumpur     1381830   3.151696  101.694237         100   
66                       Sofia     1277000  42.697863   23.322179         100   
67                      Prague     1241664  50.087465   14.421254         100   
70                      Dublin     1173179  53.349764   -6.260273         100   
71                 Kuwait City     1171880  29.379709   47.973563         100   
73               Santo Domingo     1111838  18.480197  -69.942111         100   
78                     Tbilisi     1044993  41.693459   44.801449         100   
84                   Kathmandu     1003285  27.708796   85.320244          69   
85                   Stockholm      962154  59.325117   18.071093         100   
87                      Ottawa      934243  45.421106  -75.690308         100   
88                     Managua      926883  12.146124  -86.273717         100   
90                 Ulaanbaatar      907802  47.918468  106.917702          62   
92                   Amsterdam      855965  52.372760 